In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import to_timestamp,col

"""1.Ingest sample order data into a Spark DataFrame."""

spark=SparkSession.builder.getOrCreate()

df=spark.read.csv("/Volumes/charishma_s/default/chubb/orders_dataset.csv",header=True,inferSchema=True)

df.printSchema()
display(df.limit(10))

root
 |-- order_id: string (nullable = true)
 |-- order_timestamp: timestamp (nullable = true)
 |-- customer_id: string (nullable = true)
 |-- country: string (nullable = true)
 |-- amount: double (nullable = true)
 |-- currency: string (nullable = true)
 |-- status: string (nullable = true)



order_id order_timestamp customer_id country amount currency status ORD100000 2025-01-30T09:29:00Z CUST3871 CA 420.48 INR CANCELLED ORD100001 2025-01-12T23:39:00Z CUST5772 UK 23.95 USD PAID ORD100002 2025-01-18T07:58:00Z CUST5426 DE 332.6 EUR CREATED ORD100003 2025-01-16T13:52:00Z CUST8047 AU 7.54 GBP CANCELLED ORD100004 2025-01-08T00:19:00Z CUST4794 DE 304.45 CAD CANCELLED ORD100005 2025-01-16T18:30:00Z CUST5063 CA 191.96 USD CREATED ORD100006 2025-01-18T09:38:00Z CUST7434 UK 499.38 INR PAID ORD100007 2025-01-08T12:43:00Z CUST2039 UK 453.93 INR PAID ORD100008 2025-01-05T17:04:00Z CUST8651 US 342.09 CAD PAID ORD100009 2025-01-27T18:47:00Z CUST5500 DE 360.16 INR CANCELLED

In [0]:
"""2.Add a derived column order_date (date only from order_timestamp)."""

from pyspark.sql.functions import to_date

new_df=df.withColumn('order_timestamp',to_timestamp(col('order_timestamp'))) \
        .withColumn('order_date',to_date(col('order_timestamp')))

display(new_df.limit(10))

order_id order_timestamp customer_id country amount currency status order_date ORD100000 2025-01-30T09:29:00Z CUST3871 CA 420.48 INR CANCELLED 2025-01-30 ORD100001 2025-01-12T23:39:00Z CUST5772 UK 23.95 USD PAID 2025-01-12 ORD100002 2025-01-18T07:58:00Z CUST5426 DE 332.6 EUR CREATED 2025-01-18 ORD100003 2025-01-16T13:52:00Z CUST8047 AU 7.54 GBP CANCELLED 2025-01-16 ORD100004 2025-01-08T00:19:00Z CUST4794 DE 304.45 CAD CANCELLED 2025-01-08 ORD100005 2025-01-16T18:30:00Z CUST5063 CA 191.96 USD CREATED 2025-01-16 ORD100006 2025-01-18T09:38:00Z CUST7434 UK 499.38 INR PAID 2025-01-18 ORD100007 2025-01-08T12:43:00Z CUST2039 UK 453.93 INR PAID 2025-01-08 ORD100008 2025-01-05T17:04:00Z CUST8651 US 342.09 CAD PAID 2025-01-05 ORD100009 2025-01-27T18:47:00Z CUST5500 DE 360.16 INR CANCELLED 2025-01-27

In [0]:
"""3.Write the DataFrame as a Delta table partitioned by country and order_date."""

delta_path = "/mnt/delta/orders_dataset_delta"

(new_df.write
     .format("delta")
     .mode("overwrite")
     .partitionBy("country", "order_date")
     .option("overwriteSchema", "true")
     .save(delta_path))


In [0]:
"""4.Verify the partition structure in the storage path."""

display(dbutils.fs.ls(delta_path))

display(dbutils.fs.ls(delta_path + "/country=UK"))

path name size modificationTime dbfs:/mnt/delta/orders_dataset_delta/_delta_log/ _delta_log/ 0 1764608480000 dbfs:/mnt/delta/orders_dataset_delta/country=AU/ country=AU/ 0 1764608481000 dbfs:/mnt/delta/orders_dataset_delta/country=CA/ country=CA/ 0 1764608482000 dbfs:/mnt/delta/orders_dataset_delta/country=DE/ country=DE/ 0 1764608485000 dbfs:/mnt/delta/orders_dataset_delta/country=IN/ country=IN/ 0 1764608481000 dbfs:/mnt/delta/orders_dataset_delta/country=SG/ country=SG/ 0 1764608483000 dbfs:/mnt/delta/orders_dataset_delta/country=UK/ country=UK/ 0 1764608482000 dbfs:/mnt/delta/orders_dataset_delta/country=US/ country=US/ 0 1764608482000

path name size modificationTime dbfs:/mnt/delta/orders_dataset_delta/country=UK/order_date=2025-01-01/ order_date=2025-01-01/ 0 1764608486000 dbfs:/mnt/delta/orders_dataset_delta/country=UK/order_date=2025-01-02/ order_date=2025-01-02/ 0 1764608500000 dbfs:/mnt/delta/orders_dataset_delta/country=UK/order_date=2025-01-03/ order_date=2025-01-03/ 0 1764608504000 dbfs:/mnt/delta/orders_dataset_delta/country=UK/order_date=2025-01-04/ order_date=2025-01-04/ 0 1764608504000 dbfs:/mnt/delta/orders_dataset_delta/country=UK/order_date=2025-01-05/ order_date=2025-01-05/ 0 1764608486000 dbfs:/mnt/delta/orders_dataset_delta/country=UK/order_date=2025-01-06/ order_date=2025-01-06/ 0 1764608502000 dbfs:/mnt/delta/orders_dataset_delta/country=UK/order_date=2025-01-07/ order_date=2025-01-07/ 0 1764608501000 dbfs:/mnt/delta/orders_dataset_delta/country=UK/order_date=2025-01-08/ order_date=2025-01-08/ 0 1764608506000 dbfs:/mnt/delta/orders_dataset_delta/country=UK/order_date=2025-01-09/ order_date=2025-01-09/ 0 1764608507000 dbfs:/mnt/delta/orders_dataset_delta/country=UK/order_date=2025-01-10/ order_date=2025-01-10/ 0 1764608492000 dbfs:/mnt/delta/orders_dataset_delta/country=UK/order_date=2025-01-11/ order_date=2025-01-11/ 0 1764608492000 dbfs:/mnt/delta/orders_dataset_delta/country=UK/order_date=2025-01-12/ order_date=2025-01-12/ 0 1764608494000 dbfs:/mnt/delta/orders_dataset_delta/country=UK/order_date=2025-01-13/ order_date=2025-01-13/ 0 1764608482000 dbfs:/mnt/delta/orders_dataset_delta/country=UK/order_date=2025-01-14/ order_date=2025-01-14/ 0 1764608494000 dbfs:/mnt/delta/orders_dataset_delta/country=UK/order_date=2025-01-15/ order_date=2025-01-15/ 0 1764608492000 dbfs:/mnt/delta/orders_dataset_delta/country=UK/order_date=2025-01-16/ order_date=2025-01-16/ 0 1764608502000 dbfs:/mnt/delta/orders_dataset_delta/country=UK/order_date=2025-01-17/ order_date=2025-01-17/ 0 1764608512000 dbfs:/mnt/delta/orders_dataset_delta/country=UK/order_date=2025-01-18/ order_date=2025-01-18/ 0 1764608490000 dbfs:/mnt/delta/orders_dataset_delta/country=UK/order_date=2025-01-19/ order_date=2025-01-19/ 0 1764608487000 dbfs:/mnt/delta/orders_dataset_delta/country=UK/order_date=2025-01-20/ order_date=2025-01-20/ 0 1764608506000 dbfs:/mnt/delta/orders_dataset_delta/country=UK/order_date=2025-01-21/ order_date=2025-01-21/ 0 1764608488000 dbfs:/mnt/delta/orders_dataset_delta/country=UK/order_date=2025-01-22/ order_date=2025-01-22/ 0 1764608489000 dbfs:/mnt/delta/orders_dataset_delta/country=UK/order_date=2025-01-23/ order_date=2025-01-23/ 0 1764608512000 dbfs:/mnt/delta/orders_dataset_delta/country=UK/order_date=2025-01-24/ order_date=2025-01-24/ 0 1764608497000 dbfs:/mnt/delta/orders_dataset_delta/country=UK/order_date=2025-01-25/ order_date=2025-01-25/ 0 1764608490000 dbfs:/mnt/delta/orders_dataset_delta/country=UK/order_date=2025-01-26/ order_date=2025-01-26/ 0 1764608507000 dbfs:/mnt/delta/orders_dataset_delta/country=UK/order_date=2025-01-27/ order_date=2025-01-27/ 0 1764608508000 dbfs:/mnt/delta/orders_dataset_delta/country=UK/order_date=2025-01-28/ order_date=2025-01-28/ 0 1764608501000 dbfs:/mnt/delta/orders_dataset_delta/country=UK/order_date=2025-01-29/ order_date=2025-01-29/ 0 1764608496000 dbfs:/mnt/delta/orders_dataset_delta/country=UK/order_date=2025-01-30/ order_date=2025-01-30/ 0 1764608487000

In [0]:
"""5.Run queries that demonstrate partition pruning (e.g., filter on a single country and/or date)."""

delta_table=spark.read.format("delta").load(delta_path)

#filter on single country
display(delta_table.filter("country='UK'"))

#filter on single date
display(delta_table.filter("order_date='2025-01-10'"))

#filter on both country and date
display(delta_table.filter("country='UK' AND order_date='2025-01-10'"))

#filter on country or date
display(delta_table.filter("country='UK' OR order_date='2025-01-10'"))

order_id order_timestamp customer_id country amount currency status order_date ORD100994 2025-01-10T05:11:00Z CUST6274 UK 253.14 GBP CANCELLED 2025-01-10 ORD100918 2025-01-10T15:07:00Z CUST3040 UK 201.57 USD CREATED 2025-01-10 ORD100805 2025-01-10T17:24:00Z CUST1402 UK 301.9 EUR CREATED 2025-01-10 ORD100742 2025-01-10T23:01:00Z CUST2695 UK 454.06 GBP CANCELLED 2025-01-10 ORD100693 2025-01-10T04:32:00Z CUST6468 UK 30.09 CAD CREATED 2025-01-10 ORD100374 2025-01-10T11:17:00Z CUST3809 UK 387.67 USD CANCELLED 2025-01-10 ORD100373 2025-01-10T05:47:00Z CUST1743 UK 124.98 EUR CREATED 2025-01-10 ORD100330 2025-01-10T09:46:00Z CUST2447 UK 158.37 GBP CREATED 2025-01-10 ORD100135 2025-01-10T23:56:00Z CUST2598 UK 322.07 INR CREATED 2025-01-10 ORD100122 2025-01-10T00:30:00Z CUST6970 UK 343.35 CAD CANCELLED 2025-01-10 ORD100951 2025-01-13T03:45:00Z CUST7706 UK 401.03 GBP CREATED 2025-01-13 ORD100752 2025-01-13T19:31:00Z CUST2682 UK 468.72 EUR PAID 2025-01-13 ORD100679 2025-01-13T12:34:00Z CUST9508 UK 471.97 USD CREATED 2025-01-13 ORD100493 2025-01-13T05:36:00Z CUST2123 UK 365.68 EUR CREATED 2025-01-13 ORD100443 2025-01-13T06:31:00Z CUST2821 UK 484.05 GBP PAID 2025-01-13 ORD100331 2025-01-13T18:07:00Z CUST2535 UK 67.45 CAD CANCELLED 2025-01-13 ORD100271 2025-01-13T06:03:00Z CUST9494 UK 130.49 EUR CREATED 2025-01-13 ORD100254 2025-01-13T14:36:00Z CUST8756 UK 288.24 CAD CANCELLED 2025-01-13 ORD100109 2025-01-13T19:31:00Z CUST7830 UK 407.8 CAD CANCELLED 2025-01-13 ORD100839 2025-01-14T03:03:00Z CUST9187 UK 16.05 EUR PAID 2025-01-14 ORD100831 2025-01-14T09:18:00Z CUST1753 UK 49.22 GBP CREATED 2025-01-14 ORD100823 2025-01-14T23:49:00Z CUST3739 UK 418.4 INR CANCELLED 2025-01-14 ORD100407 2025-01-14T04:30:00Z CUST6658 UK 444.45 GBP CANCELLED 2025-01-14 ORD100399 2025-01-14T04:02:00Z CUST8351 UK 321.91 CAD PAID 2025-01-14 ORD100233 2025-01-14T21:54:00Z CUST3125 UK 476.93 EUR CREATED 2025-01-14 ORD100174 2025-01-14T20:11:00Z CUST8104 UK 173.4 GBP CANCELLED 2025-01-14 ORD100011 2025-01-14T14:37:00Z CUST6332 UK 497.53 EUR CANCELLED 2025-01-14 ORD100844 2025-01-08T07:40:00Z CUST3870 UK 282.52 GBP CREATED 2025-01-08 ORD100662 2025-01-08T18:21:00Z CUST4998 UK 94.45 INR PAID 2025-01-08 ORD100363 2025-01-08T18:58:00Z CUST5184 UK 150.96 CAD PAID 2025-01-08 ORD100322 2025-01-08T07:06:00Z CUST5517 UK 126.49 INR CREATED 2025-01-08 ORD100321 2025-01-08T14:19:00Z CUST2229 UK 130.85 GBP PAID 2025-01-08 ORD100236 2025-01-08T15:41:00Z CUST3598 UK 425.26 GBP CANCELLED 2025-01-08 ORD100073 2025-01-08T21:44:00Z CUST4336 UK 245.14 CAD CREATED 2025-01-08 ORD100007 2025-01-08T12:43:00Z CUST2039 UK 453.93 INR PAID 2025-01-08 ORD100719 2025-01-09T15:55:00Z CUST7729 UK 73.63 INR CANCELLED 2025-01-09 ORD100710 2025-01-09T13:55:00Z CUST5124 UK 475.21 INR CANCELLED 2025-01-09 ORD100578 2025-01-09T19:40:00Z CUST5523 UK 406.33 EUR CANCELLED 2025-01-09 ORD100507 2025-01-09T02:57:00Z CUST4464 UK 378.82 CAD CREATED 2025-01-09 ORD100409 2025-01-09T14:57:00Z CUST5667 UK 45.77 CAD PAID 2025-01-09 ORD100107 2025-01-09T09:17:00Z CUST4439 UK 445.48 GBP CREATED 2025-01-09 ORD100091 2025-01-09T08:18:00Z CUST1042 UK 274.25 EUR CREATED 2025-01-09 ORD100025 2025-01-09T15:01:00Z CUST5621 UK 164.75 GBP CREATED 2025-01-09 ORD100876 2025-01-29T23:20:00Z CUST3258 UK 259.28 GBP PAID 2025-01-29 ORD100841 2025-01-29T09:52:00Z CUST4731 UK 246.26 EUR PAID 2025-01-29 ORD100832 2025-01-29T15:36:00Z CUST9457 UK 404.09 INR CANCELLED 2025-01-29 ORD100509 2025-01-29T08:40:00Z CUST8245 UK 271.42 EUR CREATED 2025-01-29 ORD100195 2025-01-29T15:45:00Z CUST2853 UK 345.37 EUR CREATED 2025-01-29 ORD100190 2025-01-29T03:33:00Z CUST5975 UK 116.12 USD PAID 2025-01-29 ORD100093 2025-01-29T02:11:00Z CUST3578 UK 150.65 CAD CANCELLED 2025-01-29 ORD100974 2025-01-01T19:47:00Z CUST9637 UK 312.23 EUR PAID 2025-01-01 ORD100723 2025-01-01T12:11:00Z CUST4399 UK 251.71 GBP PAID 2025-01-01 ORD100487 2025-01-01T03:51:00Z CUST7019 UK 240.61 CAD CANCELLED 2025-01-01 ORD100371 2025-01-01T13:45:00Z CUST5782 UK 432.43 EUR CANCELLED 2025-

order_id order_timestamp customer_id country amount currency status order_date ORD100994 2025-01-10T05:11:00Z CUST6274 UK 253.14 GBP CANCELLED 2025-01-10 ORD100918 2025-01-10T15:07:00Z CUST3040 UK 201.57 USD CREATED 2025-01-10 ORD100805 2025-01-10T17:24:00Z CUST1402 UK 301.9 EUR CREATED 2025-01-10 ORD100742 2025-01-10T23:01:00Z CUST2695 UK 454.06 GBP CANCELLED 2025-01-10 ORD100693 2025-01-10T04:32:00Z CUST6468 UK 30.09 CAD CREATED 2025-01-10 ORD100374 2025-01-10T11:17:00Z CUST3809 UK 387.67 USD CANCELLED 2025-01-10 ORD100373 2025-01-10T05:47:00Z CUST1743 UK 124.98 EUR CREATED 2025-01-10 ORD100330 2025-01-10T09:46:00Z CUST2447 UK 158.37 GBP CREATED 2025-01-10 ORD100135 2025-01-10T23:56:00Z CUST2598 UK 322.07 INR CREATED 2025-01-10 ORD100122 2025-01-10T00:30:00Z CUST6970 UK 343.35 CAD CANCELLED 2025-01-10 ORD100901 2025-01-10T06:01:00Z CUST6443 SG 415.89 GBP CANCELLED 2025-01-10 ORD100888 2025-01-10T03:41:00Z CUST5366 SG 251.98 INR PAID 2025-01-10 ORD100843 2025-01-10T20:23:00Z CUST2099 SG 185.32 INR PAID 2025-01-10 ORD100729 2025-01-10T10:30:00Z CUST2433 SG 147.12 GBP CANCELLED 2025-01-10 ORD100494 2025-01-10T03:26:00Z CUST6058 SG 306.81 CAD CANCELLED 2025-01-10 ORD100419 2025-01-10T01:29:00Z CUST8588 SG 259.18 EUR CANCELLED 2025-01-10 ORD100400 2025-01-10T01:42:00Z CUST6282 SG 385.08 EUR PAID 2025-01-10 ORD100212 2025-01-10T15:51:00Z CUST2489 SG 460.57 EUR CANCELLED 2025-01-10 ORD100986 2025-01-10T15:32:00Z CUST3447 CA 261.59 USD CREATED 2025-01-10 ORD100968 2025-01-10T07:56:00Z CUST4608 CA 139.39 GBP CANCELLED 2025-01-10 ORD100892 2025-01-10T23:55:00Z CUST9307 CA 294.62 INR CREATED 2025-01-10 ORD100784 2025-01-10T01:25:00Z CUST7510 CA 149.49 USD PAID 2025-01-10 ORD100741 2025-01-10T00:46:00Z CUST7549 CA 492.49 EUR PAID 2025-01-10 ORD100253 2025-01-10T23:41:00Z CUST1680 CA 364.59 CAD PAID 2025-01-10 ORD100136 2025-01-10T05:22:00Z CUST8466 CA 230.71 EUR CREATED 2025-01-10 ORD100936 2025-01-10T17:49:00Z CUST7970 AU 246.02 CAD PAID 2025-01-10 ORD100930 2025-01-10T18:07:00Z CUST4255 AU 280.95 INR PAID 2025-01-10 ORD100392 2025-01-10T11:32:00Z CUST6154 AU 10.68 EUR PAID 2025-01-10 ORD100337 2025-01-10T03:06:00Z CUST7941 AU 455.75 CAD PAID 2025-01-10 ORD100200 2025-01-10T19:30:00Z CUST8693 AU 321.1 USD PAID 2025-01-10 ORD100066 2025-01-10T20:40:00Z CUST6943 AU 207.58 INR PAID 2025-01-10 ORD100629 2025-01-10T20:14:00Z CUST1020 IN 447.69 CAD PAID 2025-01-10 ORD100599 2025-01-10T00:19:00Z CUST3336 IN 205.63 INR CANCELLED 2025-01-10 ORD100411 2025-01-10T05:14:00Z CUST7571 IN 140.83 INR CANCELLED 2025-01-10 ORD100175 2025-01-10T13:38:00Z CUST6213 IN 459.13 USD CANCELLED 2025-01-10 ORD100998 2025-01-10T22:32:00Z CUST3642 DE 96.68 INR PAID 2025-01-10 ORD100816 2025-01-10T05:00:00Z CUST2234 DE 38.24 CAD CANCELLED 2025-01-10 ORD100090 2025-01-10T18:04:00Z CUST6008 DE 487.51 CAD CREATED 2025-01-10 ORD100824 2025-01-10T18:59:00Z CUST8694 US 51.39 GBP CANCELLED 2025-01-10 ORD100781 2025-01-10T09:39:00Z CUST8119 US 93.72 EUR CREATED 2025-01-10 ORD100032 2025-01-10T08:24:00Z CUST3447 US 485.43 EUR PAID 2025-01-10

order_id order_timestamp customer_id country amount currency status order_date ORD100994 2025-01-10T05:11:00Z CUST6274 UK 253.14 GBP CANCELLED 2025-01-10 ORD100918 2025-01-10T15:07:00Z CUST3040 UK 201.57 USD CREATED 2025-01-10 ORD100805 2025-01-10T17:24:00Z CUST1402 UK 301.9 EUR CREATED 2025-01-10 ORD100742 2025-01-10T23:01:00Z CUST2695 UK 454.06 GBP CANCELLED 2025-01-10 ORD100693 2025-01-10T04:32:00Z CUST6468 UK 30.09 CAD CREATED 2025-01-10 ORD100374 2025-01-10T11:17:00Z CUST3809 UK 387.67 USD CANCELLED 2025-01-10 ORD100373 2025-01-10T05:47:00Z CUST1743 UK 124.98 EUR CREATED 2025-01-10 ORD100330 2025-01-10T09:46:00Z CUST2447 UK 158.37 GBP CREATED 2025-01-10 ORD100135 2025-01-10T23:56:00Z CUST2598 UK 322.07 INR CREATED 2025-01-10 ORD100122 2025-01-10T00:30:00Z CUST6970 UK 343.35 CAD CANCELLED 2025-01-10

order_id order_timestamp customer_id country amount currency status order_date ORD100994 2025-01-10T05:11:00Z CUST6274 UK 253.14 GBP CANCELLED 2025-01-10 ORD100918 2025-01-10T15:07:00Z CUST3040 UK 201.57 USD CREATED 2025-01-10 ORD100805 2025-01-10T17:24:00Z CUST1402 UK 301.9 EUR CREATED 2025-01-10 ORD100742 2025-01-10T23:01:00Z CUST2695 UK 454.06 GBP CANCELLED 2025-01-10 ORD100693 2025-01-10T04:32:00Z CUST6468 UK 30.09 CAD CREATED 2025-01-10 ORD100374 2025-01-10T11:17:00Z CUST3809 UK 387.67 USD CANCELLED 2025-01-10 ORD100373 2025-01-10T05:47:00Z CUST1743 UK 124.98 EUR CREATED 2025-01-10 ORD100330 2025-01-10T09:46:00Z CUST2447 UK 158.37 GBP CREATED 2025-01-10 ORD100135 2025-01-10T23:56:00Z CUST2598 UK 322.07 INR CREATED 2025-01-10 ORD100122 2025-01-10T00:30:00Z CUST6970 UK 343.35 CAD CANCELLED 2025-01-10 ORD100951 2025-01-13T03:45:00Z CUST7706 UK 401.03 GBP CREATED 2025-01-13 ORD100752 2025-01-13T19:31:00Z CUST2682 UK 468.72 EUR PAID 2025-01-13 ORD100679 2025-01-13T12:34:00Z CUST9508 UK 471.97 USD CREATED 2025-01-13 ORD100493 2025-01-13T05:36:00Z CUST2123 UK 365.68 EUR CREATED 2025-01-13 ORD100443 2025-01-13T06:31:00Z CUST2821 UK 484.05 GBP PAID 2025-01-13 ORD100331 2025-01-13T18:07:00Z CUST2535 UK 67.45 CAD CANCELLED 2025-01-13 ORD100271 2025-01-13T06:03:00Z CUST9494 UK 130.49 EUR CREATED 2025-01-13 ORD100254 2025-01-13T14:36:00Z CUST8756 UK 288.24 CAD CANCELLED 2025-01-13 ORD100109 2025-01-13T19:31:00Z CUST7830 UK 407.8 CAD CANCELLED 2025-01-13 ORD100839 2025-01-14T03:03:00Z CUST9187 UK 16.05 EUR PAID 2025-01-14 ORD100831 2025-01-14T09:18:00Z CUST1753 UK 49.22 GBP CREATED 2025-01-14 ORD100823 2025-01-14T23:49:00Z CUST3739 UK 418.4 INR CANCELLED 2025-01-14 ORD100407 2025-01-14T04:30:00Z CUST6658 UK 444.45 GBP CANCELLED 2025-01-14 ORD100399 2025-01-14T04:02:00Z CUST8351 UK 321.91 CAD PAID 2025-01-14 ORD100233 2025-01-14T21:54:00Z CUST3125 UK 476.93 EUR CREATED 2025-01-14 ORD100174 2025-01-14T20:11:00Z CUST8104 UK 173.4 GBP CANCELLED 2025-01-14 ORD100011 2025-01-14T14:37:00Z CUST6332 UK 497.53 EUR CANCELLED 2025-01-14 ORD100844 2025-01-08T07:40:00Z CUST3870 UK 282.52 GBP CREATED 2025-01-08 ORD100662 2025-01-08T18:21:00Z CUST4998 UK 94.45 INR PAID 2025-01-08 ORD100363 2025-01-08T18:58:00Z CUST5184 UK 150.96 CAD PAID 2025-01-08 ORD100322 2025-01-08T07:06:00Z CUST5517 UK 126.49 INR CREATED 2025-01-08 ORD100321 2025-01-08T14:19:00Z CUST2229 UK 130.85 GBP PAID 2025-01-08 ORD100236 2025-01-08T15:41:00Z CUST3598 UK 425.26 GBP CANCELLED 2025-01-08 ORD100073 2025-01-08T21:44:00Z CUST4336 UK 245.14 CAD CREATED 2025-01-08 ORD100007 2025-01-08T12:43:00Z CUST2039 UK 453.93 INR PAID 2025-01-08 ORD100719 2025-01-09T15:55:00Z CUST7729 UK 73.63 INR CANCELLED 2025-01-09 ORD100710 2025-01-09T13:55:00Z CUST5124 UK 475.21 INR CANCELLED 2025-01-09 ORD100578 2025-01-09T19:40:00Z CUST5523 UK 406.33 EUR CANCELLED 2025-01-09 ORD100507 2025-01-09T02:57:00Z CUST4464 UK 378.82 CAD CREATED 2025-01-09 ORD100409 2025-01-09T14:57:00Z CUST5667 UK 45.77 CAD PAID 2025-01-09 ORD100107 2025-01-09T09:17:00Z CUST4439 UK 445.48 GBP CREATED 2025-01-09 ORD100091 2025-01-09T08:18:00Z CUST1042 UK 274.25 EUR CREATED 2025-01-09 ORD100025 2025-01-09T15:01:00Z CUST5621 UK 164.75 GBP CREATED 2025-01-09 ORD100901 2025-01-10T06:01:00Z CUST6443 SG 415.89 GBP CANCELLED 2025-01-10 ORD100888 2025-01-10T03:41:00Z CUST5366 SG 251.98 INR PAID 2025-01-10 ORD100843 2025-01-10T20:23:00Z CUST2099 SG 185.32 INR PAID 2025-01-10 ORD100729 2025-01-10T10:30:00Z CUST2433 SG 147.12 GBP CANCELLED 2025-01-10 ORD100494 2025-01-10T03:26:00Z CUST6058 SG 306.81 CAD CANCELLED 2025-01-10 ORD100419 2025-01-10T01:29:00Z CUST8588 SG 259.18 EUR CANCELLED 2025-01-10 ORD100400 2025-01-10T01:42:00Z CUST6282 SG 385.08 EUR PAID 2025-01-10 ORD100212 2025-01-10T15:51:00Z CUST2489 SG 460.57 EUR CANCELLED 2025-01-10 ORD100986 2025-01-10T15:32:00Z CUST3447 CA 261.59 USD CREATED 2025-01-10 ORD100968 2025-01-10T07:56:00Z CUST4608 CA 139.39 GBP CANCELLED 2025-01-10 ORD100892 2025-01-10T23:55:00Z CUST9307 CA 294.62 INR CRE

In [0]:
"""6.Demonstrate Delta Lake Time Travel:Write data, update some rows, then query older versions."""

from delta.tables import DeltaTable
d_tb=DeltaTable.forPath(spark,delta_path)

d_tb.history().show()

#update some rows
d_tb.update("country='UK' AND order_date='2025-01-10'",{'status': lit('shipped')})
d_tb.history().show()

#query older versions   
display(d_tb.history().filter("version=0"))

old_version_df = spark.read.format("delta").option("versionAsOf", 0).load(delta_path)
display(old_version_df)



+-------+-------------------+---------------+--------------------+---------+--------------------+----+------------------+--------------------+-----------+-----------------+-------------+--------------------+------------+--------------------+
|version|          timestamp|         userId|            userName|operation| operationParameters| job|          notebook|           clusterId|readVersion|   isolationLevel|isBlindAppend|    operationMetrics|userMetadata|          engineInfo|
+-------+-------------------+---------------+--------------------+---------+--------------------+----+------------------+--------------------+-----------+-----------------+-------------+--------------------+------------+--------------------+
|     23|2025-12-01 18:46:09|148593850855805|s.vijaya.charishm...|   DELETE|{predicate -> ["(...|NULL|{2065271677097478}|1121-101913-kir4gy3f|         22|WriteSerializable|        false|{numRemovedFiles ...|        NULL|Databricks-Runtim...|
|     22|2025-12-01 18:46:07|148

version timestamp userId userName operation operationParameters job notebook clusterId readVersion isolationLevel isBlindAppend operationMetrics userMetadata engineInfo 0 2025-12-01T17:01:55Z 148593850855805 s.vijaya.charishma@gmail.com WRITE Map(mode -> Overwrite, statsOnLoad -> false, partitionBy -> ["country","order_date"]) null List(2065271677097478) 1121-101913-kir4gy3f null WriteSerializable false Map(numFiles -> 207, numRemovedFiles -> 0, numRemovedBytes -> 0, numDeletionVectorsRemoved -> 0, numOutputRows -> 1000, numOutputBytes -> 398797) null Databricks-Runtime/17.3.x-photon-scala2.13

order_id order_timestamp customer_id country amount currency status order_date ORD100999 2025-01-25T11:17:00Z CUST5823 SG 226.45 CAD PAID 2025-01-25 ORD100961 2025-01-25T15:43:00Z CUST5571 SG 203.37 USD CANCELLED 2025-01-25 ORD100732 2025-01-25T14:58:00Z CUST8094 SG 333.13 EUR CREATED 2025-01-25 ORD100706 2025-01-25T08:01:00Z CUST5968 SG 105.43 INR PAID 2025-01-25 ORD100564 2025-01-25T08:29:00Z CUST4212 SG 89.91 GBP CREATED 2025-01-25 ORD100531 2025-01-25T21:50:00Z CUST8527 SG 287.12 INR PAID 2025-01-25 ORD100499 2025-01-25T19:52:00Z CUST1139 SG 6.48 USD PAID 2025-01-25 ORD100260 2025-01-25T20:10:00Z CUST9709 SG 61.66 EUR CREATED 2025-01-25 ORD100246 2025-01-25T23:35:00Z CUST6653 SG 133.72 INR CANCELLED 2025-01-25 ORD100178 2025-01-25T02:10:00Z CUST9861 SG 478.11 USD CANCELLED 2025-01-25 ORD100101 2025-01-25T17:42:00Z CUST1429 SG 291.52 EUR CANCELLED 2025-01-25 ORD100991 2025-01-08T19:55:00Z CUST2750 IN 59.42 USD CREATED 2025-01-08 ORD100939 2025-01-08T11:57:00Z CUST2241 IN 181.3 CAD CANCELLED 2025-01-08 ORD100913 2025-01-08T11:59:00Z CUST7042 IN 289.29 EUR CANCELLED 2025-01-08 ORD100646 2025-01-08T17:47:00Z CUST8470 IN 177.73 INR CREATED 2025-01-08 ORD100474 2025-01-08T03:05:00Z CUST5265 IN 118.37 USD CREATED 2025-01-08 ORD100417 2025-01-08T16:01:00Z CUST4852 IN 382.46 INR CANCELLED 2025-01-08 ORD100181 2025-01-08T07:42:00Z CUST6599 IN 53.08 EUR PAID 2025-01-08 ORD100152 2025-01-08T22:54:00Z CUST9560 IN 156.96 GBP CANCELLED 2025-01-08 ORD100105 2025-01-08T00:45:00Z CUST6969 IN 42.18 INR PAID 2025-01-08 ORD100049 2025-01-08T19:32:00Z CUST5454 IN 164.32 GBP PAID 2025-01-08 ORD100045 2025-01-08T02:09:00Z CUST4408 IN 75.07 CAD PAID 2025-01-08 ORD100994 2025-01-10T05:11:00Z CUST6274 UK 253.14 GBP CANCELLED 2025-01-10 ORD100918 2025-01-10T15:07:00Z CUST3040 UK 201.57 USD CREATED 2025-01-10 ORD100805 2025-01-10T17:24:00Z CUST1402 UK 301.9 EUR CREATED 2025-01-10 ORD100742 2025-01-10T23:01:00Z CUST2695 UK 454.06 GBP CANCELLED 2025-01-10 ORD100693 2025-01-10T04:32:00Z CUST6468 UK 30.09 CAD CREATED 2025-01-10 ORD100374 2025-01-10T11:17:00Z CUST3809 UK 387.67 USD CANCELLED 2025-01-10 ORD100373 2025-01-10T05:47:00Z CUST1743 UK 124.98 EUR CREATED 2025-01-10 ORD100330 2025-01-10T09:46:00Z CUST2447 UK 158.37 GBP CREATED 2025-01-10 ORD100135 2025-01-10T23:56:00Z CUST2598 UK 322.07 INR CREATED 2025-01-10 ORD100122 2025-01-10T00:30:00Z CUST6970 UK 343.35 CAD CANCELLED 2025-01-10 ORD100940 2025-01-07T00:58:00Z CUST6137 SG 402.27 EUR CREATED 2025-01-07 ORD100850 2025-01-07T13:27:00Z CUST6358 SG 46.33 GBP PAID 2025-01-07 ORD100842 2025-01-07T21:52:00Z CUST3895 SG 58.62 INR CREATED 2025-01-07 ORD100713 2025-01-07T21:01:00Z CUST9103 SG 286.62 CAD CREATED 2025-01-07 ORD100627 2025-01-07T02:53:00Z CUST5115 SG 364.93 GBP CANCELLED 2025-01-07 ORD100617 2025-01-07T21:11:00Z CUST8448 SG 61.91 USD CANCELLED 2025-01-07 ORD100533 2025-01-07T20:30:00Z CUST7508 SG 289.41 GBP CREATED 2025-01-07 ORD100300 2025-01-07T00:49:00Z CUST1003 SG 258.85 GBP CREATED 2025-01-07 ORD100179 2025-01-07T02:55:00Z CUST8668 SG 19.19 INR CANCELLED 2025-01-07 ORD100114 2025-01-07T15:51:00Z CUST5014 SG 194.19 USD CREATED 2025-01-07 ORD100963 2025-01-27T12:46:00Z CUST8755 DE 127.1 INR CREATED 2025-01-27 ORD100959 2025-01-27T01:57:00Z CUST3063 DE 143.79 CAD CANCELLED 2025-01-27 ORD100633 2025-01-27T02:56:00Z CUST6711 DE 491.01 GBP CANCELLED 2025-01-27 ORD100571 2025-01-27T15:30:00Z CUST9371 DE 360.05 CAD PAID 2025-01-27 ORD100553 2025-01-27T10:27:00Z CUST6526 DE 298.96 USD CREATED 2025-01-27 ORD100368 2025-01-27T06:09:00Z CUST3043 DE 430.46 INR CANCELLED 2025-01-27 ORD100165 2025-01-27T17:11:00Z CUST2495 DE 166.36 CAD CREATED 2025-01-27 ORD100146 2025-01-27T21:01:00Z CUST7756 DE 267.2 GBP CANCELLED 2025-01-27 ORD100054 2025-01-27T07:33:00Z CUST6654 DE 264.7 INR CREATED 2025-01-27 ORD100009 2025-01-27T18:47:00Z CUST5500 DE 360.16 INR CANCELLED 2025-01-27 ORD100951 2025-01-13T03:45:00Z CUST7706 UK 401.03 GBP CREATED 2025-01-13 ORD100752 2025-01-13T19:31:00Z CUST2682 UK 468.72 EUR PAID 2

In [0]:
"""7.Demonstrate Schema Evolution"""
#Add payment_method & coupon_code to new data.
from pyspark.sql.functions import lit, rand, when, col

coupon_list = ["NEW50", "SAVE10", "WELCOME20", "FREESHIP", "MEGA30"]

# create DataFrame that has two new columns
new_rows = (
    new_df
        .withColumn("payment_method", lit("CARD"))
        .withColumn(
        "coupon_code",
            when(rand() < 0.2, lit("NEW50"))
            .when(rand() < 0.4, lit("SAVE10"))
            .when(rand() < 0.6, lit("WELCOME20"))
            .when(rand() < 0.8, lit("FREESHIP"))
            .otherwise(lit("MEGA30"))
        )
)


#Write to the same Delta table, allowing schema evolution.
(new_rows
  .write
  .format("delta")
  .mode("append")
  .option("mergeSchema", "true")
  .partitionBy("country","order_date")
  .save(delta_path))

#display
new_df=spark.read.format("delta").load(delta_path)
display(new_df)



order_id order_timestamp customer_id country amount currency status order_date payment_method coupon_code ORD100066 2025-01-10T20:40:00Z CUST6943 AU 207.58 INR PAID 2025-01-10 CARD SAVE10 ORD100200 2025-01-10T19:30:00Z CUST8693 AU 321.1 USD PAID 2025-01-10 CARD SAVE10 ORD100337 2025-01-10T03:06:00Z CUST7941 AU 455.75 CAD PAID 2025-01-10 CARD NEW50 ORD100392 2025-01-10T11:32:00Z CUST6154 AU 10.68 EUR PAID 2025-01-10 CARD WELCOME20 ORD100930 2025-01-10T18:07:00Z CUST4255 AU 280.95 INR PAID 2025-01-10 CARD WELCOME20 ORD100936 2025-01-10T17:49:00Z CUST7970 AU 246.02 CAD PAID 2025-01-10 CARD NEW50 ORD100066 2025-01-10T20:40:00Z CUST6943 AU 207.58 INR PAID 2025-01-10 CARD NEW50 ORD100200 2025-01-10T19:30:00Z CUST8693 AU 321.1 USD PAID 2025-01-10 CARD FREESHIP ORD100337 2025-01-10T03:06:00Z CUST7941 AU 455.75 CAD PAID 2025-01-10 CARD NEW50 ORD100392 2025-01-10T11:32:00Z CUST6154 AU 10.68 EUR PAID 2025-01-10 CARD WELCOME20 ORD100930 2025-01-10T18:07:00Z CUST4255 AU 280.95 INR PAID 2025-01-10 CARD WELCOME20 ORD100936 2025-01-10T17:49:00Z CUST7970 AU 246.02 CAD PAID 2025-01-10 CARD SAVE10 ORD100936 2025-01-10T17:49:00Z CUST7970 AU 246.02 CAD PAID 2025-01-10 CARD NEW50 ORD100930 2025-01-10T18:07:00Z CUST4255 AU 280.95 INR PAID 2025-01-10 CARD NEW50 ORD100392 2025-01-10T11:32:00Z CUST6154 AU 10.68 EUR PAID 2025-01-10 CARD SAVE10 ORD100337 2025-01-10T03:06:00Z CUST7941 AU 455.75 CAD PAID 2025-01-10 CARD SAVE10 ORD100200 2025-01-10T19:30:00Z CUST8693 AU 321.1 USD PAID 2025-01-10 CARD FREESHIP ORD100066 2025-01-10T20:40:00Z CUST6943 AU 207.58 INR PAID 2025-01-10 CARD SAVE10 ORD100066 2025-01-10T20:40:00Z CUST6943 AU 207.58 INR PAID 2025-01-10 CARD WELCOME20 ORD100200 2025-01-10T19:30:00Z CUST8693 AU 321.1 USD PAID 2025-01-10 CARD SAVE10 ORD100337 2025-01-10T03:06:00Z CUST7941 AU 455.75 CAD PAID 2025-01-10 CARD SAVE10 ORD100392 2025-01-10T11:32:00Z CUST6154 AU 10.68 EUR PAID 2025-01-10 CARD NEW50 ORD100930 2025-01-10T18:07:00Z CUST4255 AU 280.95 INR PAID 2025-01-10 CARD SAVE10 ORD100936 2025-01-10T17:49:00Z CUST7970 AU 246.02 CAD PAID 2025-01-10 CARD WELCOME20 ORD100936 2025-01-10T17:49:00Z CUST7970 AU 246.02 CAD PAID 2025-01-10 CARD NEW50 ORD100930 2025-01-10T18:07:00Z CUST4255 AU 280.95 INR PAID 2025-01-10 CARD MEGA30 ORD100392 2025-01-10T11:32:00Z CUST6154 AU 10.68 EUR PAID 2025-01-10 CARD WELCOME20 ORD100337 2025-01-10T03:06:00Z CUST7941 AU 455.75 CAD PAID 2025-01-10 CARD WELCOME20 ORD100200 2025-01-10T19:30:00Z CUST8693 AU 321.1 USD PAID 2025-01-10 CARD SAVE10 ORD100066 2025-01-10T20:40:00Z CUST6943 AU 207.58 INR PAID 2025-01-10 CARD WELCOME20 ORD100936 2025-01-10T17:49:00Z CUST7970 AU 246.02 CAD PAID 2025-01-10 CARD FREESHIP ORD100930 2025-01-10T18:07:00Z CUST4255 AU 280.95 INR PAID 2025-01-10 CARD SAVE10 ORD100392 2025-01-10T11:32:00Z CUST6154 AU 10.68 EUR PAID 2025-01-10 CARD WELCOME20 ORD100337 2025-01-10T03:06:00Z CUST7941 AU 455.75 CAD PAID 2025-01-10 CARD WELCOME20 ORD100200 2025-01-10T19:30:00Z CUST8693 AU 321.1 USD PAID 2025-01-10 CARD SAVE10 ORD100066 2025-01-10T20:40:00Z CUST6943 AU 207.58 INR PAID 2025-01-10 CARD FREESHIP ORD100936 2025-01-10T17:49:00Z CUST7970 AU 246.02 CAD PAID 2025-01-10 CARD SAVE10 ORD100930 2025-01-10T18:07:00Z CUST4255 AU 280.95 INR PAID 2025-01-10 CARD WELCOME20 ORD100392 2025-01-10T11:32:00Z CUST6154 AU 10.68 EUR PAID 2025-01-10 CARD WELCOME20 ORD100337 2025-01-10T03:06:00Z CUST7941 AU 455.75 CAD PAID 2025-01-10 CARD WELCOME20 ORD100200 2025-01-10T19:30:00Z CUST8693 AU 321.1 USD PAID 2025-01-10 CARD MEGA30 ORD100066 2025-01-10T20:40:00Z CUST6943 AU 207.58 INR PAID 2025-01-10 CARD FREESHIP ORD100066 2025-01-10T20:40:00Z CUST6943 AU 207.58 INR PAID 2025-01-10 CARD NEW50 ORD100200 2025-01-10T19:30:00Z CUST8693 AU 321.1 USD PAID 2025-01-10 CARD FREESHIP ORD100337 2025-01-10T03:06:00Z CUST7941 AU 455.75 CAD PAID 2025-01-10 CARD NEW50 ORD100392 2025-01-10T11:32:00Z CUST6154 AU 10.68 EUR PAID 2025-01-10 CARD WELCOME20 ORD100930 2025-01-10T18:07:00Z CUST4255 AU 280.95 INR PAID 2025-01-10 CARD SAVE10 ORD100936

In [0]:
#adding payment_method and coupon_code to complete data 
from pyspark.sql.functions import lit

d_tb.update("payment_method IS NULL", {"payment_method": lit("CARD")})
d_tb.update(
    "coupon_code IS NULL",
    {
        "coupon_code": when(col("amount") >= 500, lit("MEGA30"))
                        .when(col("amount") >= 200, lit("SAVE10"))
                        .when(col("amount") >= 100, lit("WELCOME20"))
                        .otherwise(lit("FREESHIP"))
    }
)


In [0]:
"""8.Demonstrate Updates & Deletes using Delta:"""

#update
#Mark some orders as CANCELLED.
d_tb.update("country='UK' AND order_date='2025-01-20'",{"status":lit("CANCELLED")})
#display
display(d_tb.toDF().filter("country='UK' AND order_date='2025-01-20'"))


#delete
#Delete orders below a certain amount (e.g., test data cleanup)
d_tb.delete("country='US' AND order_date='2025-01-20' AND amount<100")
#display
display(d_tb.toDF().filter("country='US' AND order_date='2025-01-20' AND amount<100"))




order_id order_timestamp customer_id country amount currency status order_date payment_method coupon_code ORD100540 2025-01-20T04:22:00Z CUST4720 UK 206.75 INR CANCELLED 2025-01-20 CARD SAVE10 ORD100425 2025-01-20T08:24:00Z CUST6366 UK 286.75 GBP CANCELLED 2025-01-20 CARD SAVE10 ORD100391 2025-01-20T04:34:00Z CUST7242 UK 25.69 INR CANCELLED 2025-01-20 CARD FREESHIP ORD100391 2025-01-20T04:34:00Z CUST7242 UK 25.69 INR CANCELLED 2025-01-20 CARD FREESHIP ORD100425 2025-01-20T08:24:00Z CUST6366 UK 286.75 GBP CANCELLED 2025-01-20 CARD SAVE10 ORD100540 2025-01-20T04:22:00Z CUST4720 UK 206.75 INR CANCELLED 2025-01-20 CARD SAVE10 ORD100540 2025-01-20T04:22:00Z CUST4720 UK 206.75 INR CANCELLED 2025-01-20 CARD SAVE10 ORD100425 2025-01-20T08:24:00Z CUST6366 UK 286.75 GBP CANCELLED 2025-01-20 CARD SAVE10 ORD100391 2025-01-20T04:34:00Z CUST7242 UK 25.69 INR CANCELLED 2025-01-20 CARD FREESHIP ORD100391 2025-01-20T04:34:00Z CUST7242 UK 25.69 INR CANCELLED 2025-01-20 CARD FREESHIP ORD100425 2025-01-20T08:24:00Z CUST6366 UK 286.75 GBP CANCELLED 2025-01-20 CARD SAVE10 ORD100540 2025-01-20T04:22:00Z CUST4720 UK 206.75 INR CANCELLED 2025-01-20 CARD SAVE10 ORD100391 2025-01-20T04:34:00Z CUST7242 UK 25.69 INR CANCELLED 2025-01-20 CARD FREESHIP ORD100425 2025-01-20T08:24:00Z CUST6366 UK 286.75 GBP CANCELLED 2025-01-20 CARD SAVE10 ORD100540 2025-01-20T04:22:00Z CUST4720 UK 206.75 INR CANCELLED 2025-01-20 CARD SAVE10 ORD100540 2025-01-20T04:22:00Z CUST4720 UK 206.75 INR CANCELLED 2025-01-20 CARD SAVE10 ORD100425 2025-01-20T08:24:00Z CUST6366 UK 286.75 GBP CANCELLED 2025-01-20 CARD SAVE10 ORD100391 2025-01-20T04:34:00Z CUST7242 UK 25.69 INR CANCELLED 2025-01-20 CARD FREESHIP ORD100540 2025-01-20T04:22:00Z CUST4720 UK 206.75 INR CANCELLED 2025-01-20 CARD SAVE10 ORD100425 2025-01-20T08:24:00Z CUST6366 UK 286.75 GBP CANCELLED 2025-01-20 CARD SAVE10 ORD100391 2025-01-20T04:34:00Z CUST7242 UK 25.69 INR CANCELLED 2025-01-20 CARD FREESHIP ORD100391 2025-01-20T04:34:00Z CUST7242 UK 25.69 INR CANCELLED 2025-01-20 CARD FREESHIP ORD100425 2025-01-20T08:24:00Z CUST6366 UK 286.75 GBP CANCELLED 2025-01-20 CARD SAVE10 ORD100540 2025-01-20T04:22:00Z CUST4720 UK 206.75 INR CANCELLED 2025-01-20 CARD SAVE10 ORD100391 2025-01-20T04:34:00Z CUST7242 UK 25.69 INR CANCELLED 2025-01-20 CARD FREESHIP ORD100425 2025-01-20T08:24:00Z CUST6366 UK 286.75 GBP CANCELLED 2025-01-20 CARD SAVE10 ORD100540 2025-01-20T04:22:00Z CUST4720 UK 206.75 INR CANCELLED 2025-01-20 CARD SAVE10 ORD100391 2025-01-20T04:34:00Z CUST7242 UK 25.69 INR CANCELLED 2025-01-20 CARD FREESHIP ORD100425 2025-01-20T08:24:00Z CUST6366 UK 286.75 GBP CANCELLED 2025-01-20 CARD SAVE10 ORD100540 2025-01-20T04:22:00Z CUST4720 UK 206.75 INR CANCELLED 2025-01-20 CARD SAVE10 ORD100540 2025-01-20T04:22:00Z CUST4720 UK 206.75 INR CANCELLED 2025-01-20 CARD SAVE10 ORD100425 2025-01-20T08:24:00Z CUST6366 UK 286.75 GBP CANCELLED 2025-01-20 CARD SAVE10 ORD100391 2025-01-20T04:34:00Z CUST7242 UK 25.69 INR CANCELLED 2025-01-20 CARD FREESHIP ORD100540 2025-01-20T04:22:00Z CUST4720 UK 206.75 INR CANCELLED 2025-01-20 CARD SAVE10 ORD100425 2025-01-20T08:24:00Z CUST6366 UK 286.75 GBP CANCELLED 2025-01-20 CARD SAVE10 ORD100391 2025-01-20T04:34:00Z CUST7242 UK 25.69 INR CANCELLED 2025-01-20 CARD FREESHIP ORD100540 2025-01-20T04:22:00Z CUST4720 UK 206.75 INR CANCELLED 2025-01-20 CARD SAVE10 ORD100425 2025-01-20T08:24:00Z CUST6366 UK 286.75 GBP CANCELLED 2025-01-20 CARD SAVE10 ORD100391 2025-01-20T04:34:00Z CUST7242 UK 25.69 INR CANCELLED 2025-01-20 CARD FREESHIP ORD100540 2025-01-20T04:22:00Z CUST4720 UK 206.75 INR CANCELLED 2025-01-20 CARD SAVE10 ORD100425 2025-01-20T08:24:00Z CUST6366 UK 286.75 GBP CANCELLED 2025-01-20 CARD SAVE10 ORD100391 2025-01-20T04:34:00Z CUST7242 UK 25.69 INR CANCELLED 2025-01-20 CARD FREESHIP ORD100391 2025-01-20T04:34:00Z CUST7242 UK 25.69 INR CANCELLED 2025-01-20 CARD FREESHIP ORD100425 2025-01-20T08:24:00Z CUST6366 UK 286.75 GBP CANCELLED 2025-01-20 CARD SAVE10 ORD100540 2025-01-20T04:22:00Z CUST4720 UK 206.75 I

order_id order_timestamp customer_id country amount currency status order_date payment_method coupon_code

In [0]:
"""9.(Bonus) Optimize the table:
Use OPTIMIZE and optionally ZORDER on customer_id or order
"""

spark.sql(
    f"OPTIMIZE delta.`{delta_path}` ZORDER BY (customer_id)"
)



DataFrame[path: string, metrics: struct<numFilesAdded:bigint,numFilesRemoved:bigint,filesAdded:struct<min:bigint,max:bigint,avg:double,totalFiles:bigint,totalSize:bigint>,filesRemoved:struct<min:bigint,max:bigint,avg:double,totalFiles:bigint,totalSize:bigint>,partitionsOptimized:bigint,zOrderStats:struct<strategyName:string,inputCubeFiles:struct<num:bigint,size:bigint>,inputOtherFiles:struct<num:bigint,size:bigint>,inputNumCubes:bigint,mergedFiles:struct<num:bigint,size:bigint>,numOutputCubes:bigint,mergedNumCubes:bigint>,clusteringStats:struct<inputZCubeFiles:struct<numFiles:bigint,size:bigint>,inputOtherFiles:struct<numFiles:bigint,size:bigint>,inputNumZCubes:bigint,mergedFiles:struct<numFiles:bigint,size:bigint>,numOutputZCubes:bigint>,numBins:bigint,numBatches:bigint,totalConsideredFiles:bigint,totalFilesSkipped:bigint,preserveInsertionOrder:boolean,numFilesSkippedToReduceWriteAmplification:bigint,numBytesSkippedToReduceWriteAmplification:bigint,startTimeMs:bigint,endTimeMs:bigint,